In [1]:
import numpy as np
import torch
import sys
import os
import time
import xlwt
import csv
import random
import math
import copy
import sys 
sys.path.append("..") 

from codes.centralRepo.eegDataset import eegDataset
from codes.centralRepo.baseModel import baseModel
import codes.centralRepo.networks
import codes.centralRepo.transforms
from codes.centralRepo.saveData import fetchData
from codes.classify.train import config as cf


In [2]:
config, data, net = cf(0, 'FBCNet', 0, None)
if config['transformArguments'] is not None:
    if len(config['transformArguments']) >1 :
        transform = transforms.Compose([transforms.__dict__[key](**value) for key, value in config['transformArguments'].items()])
    else:
        transform = transforms.__dict__[list(config['transformArguments'].keys())[0]](**config['transformArguments'][list(config['transformArguments'].keys())[0]])
else:
    transform = None
print('Data loading in progress')
fetchData(os.path.dirname(config['inDataPath']), 0) # Make sure that all the required data is present!
data = eegDataset(dataPath = config['inDataPath'], dataLabelsPath= config['inLabelPath'], preloadData = config['preloadData'], transform= transform)
print('Data loading finished')

Outputs will be saved in folder : d:\codes\BCI-VR\FBCNet\output\bci42a\2023-11-25--19-16-375\
Results will be saved in folder : d:\codes\BCI-VR\FBCNet\output\bci42a\2023-11-25--19-16-375\Results
Models will be saved in folder : d:\codes\BCI-VR\FBCNet\output\bci42a\2023-11-25--19-16-375\FBCNet
None
Data loading in progress
fetch stetting:  d:\codes\BCI-VR\FBCNet\data\bci42a 0
All the data you need is present! 
Data loading finished
Trainable Parameters in the network are: 11812
ALL CONFIG COMPLETED
 ******************************
Data loading in progress
fetch stetting:  d:\codes\BCI-VR\FBCNet\data\bci42a 0
All the data you need is present! 
Data loading finished


In [3]:
def spiltDataSet(trainDataToUse, testDataToUse, validationSet, data):
    '''
    去掉标签为tongue的数据
    把T和E数据集合并,并取80%用于训练, 20%用于测试
    各subject分层采样
    Return:
    trainData: torch.DataSet类型
    valData: torch.DataSet类型
    finalTestData: list[dict]
    '''

    subs = sorted(set([d[3] for d in data.labels]))

    train_data = []
    val_data = []
    test_data = []

    # 每个个体分层采样
    for iSub, sub in enumerate(subs):
        
        # extract subject data
        subIdx = [i for i, x in enumerate(data.labels) if x[3] in sub]
        subData = copy.deepcopy(data)
        subData.createPartialDataset(subIdx, loadNonLoadedData = True)
        
        trainData = copy.deepcopy(subData)
        del subData
        testData = copy.deepcopy(trainData)
        
        # 训练集0.8，测试集0.2
        # print(len(trainData))
        # print(math.ceil(len(trainData)*config['trainDataToUse']))
        trainData.createPartialDataset(list(range(0, math.ceil(len(trainData)*config['trainDataToUse']))))
        testData.createPartialDataset(list( range( 
            math.ceil(len(testData)*(1-config['testDataToUse'])) , len(testData))))

        # 训练集再分，训练集0.8，验证集0.2
        valData = copy.deepcopy(trainData)
        valData.createPartialDataset(list( range( 
            math.ceil(len(trainData)*(1-config['validationSet'])) , len(trainData))))
        trainData.createPartialDataset(list(range(0, math.ceil(len(trainData)*(1-config['validationSet'])))))
        
        train_data.append(trainData)
        val_data.append(valData)
        test_data.append(testData)

    # 每个个体分层采样的数据合在一起
    for i in range(1, len(train_data)):
        train_data[0].combineDataset(train_data[i])
        val_data[0].combineDataset(val_data[i])
        test_data[0].combineDataset(test_data[i])

    # 得到最后的训练集、验证集和测试集
    trainData = copy.deepcopy(train_data[0])
    valData = copy.deepcopy(val_data[0])
    testData = copy.deepcopy(test_data[0])
    del train_data, val_data, test_data

    # 测试集要加上tongue标签的数据
    finalTestData = data.getTongueData()
    for sample in testData:
        finalTestData.append(sample)
    
    # print(len(trainData), len(valData), len(testData), len(finalTestData))
    # print(finalTestData[0])
    # print(finalTestData[-1])
    return trainData, valData, finalTestData

In [4]:
spiltDataSet(0.8, 0.2, 0.2, data)

2493 621 774 1296
{'data': tensor([[[ 1.1189e-02,  1.1189e-02,  1.1189e-02,  ...,  1.1189e-02,
           1.1189e-02,  1.1189e-02],
         [ 1.7988e-01,  1.7989e-01,  1.7990e-01,  ...,  1.8002e-01,
           1.8006e-01,  1.8010e-01],
         [ 1.3922e-01,  1.3932e-01,  1.3947e-01,  ...,  1.4062e-01,
           1.4106e-01,  1.4156e-01],
         ...,
         [-8.9591e+00,  1.4186e+00,  3.6813e+00,  ..., -9.8741e-01,
           8.6242e-02, -1.3536e+00],
         [-9.8349e+00,  2.2239e-01,  3.7799e+00,  ..., -2.1591e+00,
           6.5814e-01, -7.0138e-01],
         [-1.0380e+01, -8.1842e-01,  3.4511e+00,  ..., -2.2119e+00,
           8.7385e-01,  6.4747e-01]],

        [[-1.2168e-01, -1.2168e-01, -1.2168e-01,  ..., -1.2168e-01,
          -1.2168e-01, -1.2168e-01],
         [ 5.8885e-03,  5.7690e-03,  5.5912e-03,  ...,  4.3418e-03,
           3.9107e-03,  3.4401e-03],
         [-1.0690e-01, -1.0604e-01, -1.0481e-01,  ..., -9.7200e-02,
          -9.5019e-02, -9.2899e-02],
         ...

(<codes.centralRepo.eegDataset.eegDataset at 0x2124febcc88>,
 [{'data': tensor([[[ 1.1189e-02,  1.1189e-02,  1.1189e-02,  ...,  1.1189e-02,
              1.1189e-02,  1.1189e-02],
            [ 1.7988e-01,  1.7989e-01,  1.7990e-01,  ...,  1.8002e-01,
              1.8006e-01,  1.8010e-01],
            [ 1.3922e-01,  1.3932e-01,  1.3947e-01,  ...,  1.4062e-01,
              1.4106e-01,  1.4156e-01],
            ...,
            [-8.9591e+00,  1.4186e+00,  3.6813e+00,  ..., -9.8741e-01,
              8.6242e-02, -1.3536e+00],
            [-9.8349e+00,  2.2239e-01,  3.7799e+00,  ..., -2.1591e+00,
              6.5814e-01, -7.0138e-01],
            [-1.0380e+01, -8.1842e-01,  3.4511e+00,  ..., -2.2119e+00,
              8.7385e-01,  6.4747e-01]],
   
           [[-1.2168e-01, -1.2168e-01, -1.2168e-01,  ..., -1.2168e-01,
             -1.2168e-01, -1.2168e-01],
            [ 5.8885e-03,  5.7690e-03,  5.5912e-03,  ...,  4.3418e-03,
              3.9107e-03,  3.4401e-03],
            [-1.0690e

In [1]:
import numpy as np
import torch

loaded_data_list = np.load('../codes/classify/TestData.npy', allow_pickle=True)



In [5]:
loaded_data_list[-2]

{'data': array([[[-5.62232673e-01, -5.62232673e-01, -5.62232673e-01, ...,
          -5.62232673e-01, -5.62232673e-01, -5.62232673e-01],
         [-4.09150600e-01, -4.09702927e-01, -4.10524398e-01, ...,
          -4.16297436e-01, -4.18289512e-01, -4.20464069e-01],
         [-4.14953828e-01, -4.11436141e-01, -4.06353772e-01, ...,
          -3.75687480e-01, -3.67157429e-01, -3.59047890e-01],
         ...,
         [ 1.11298742e+01,  2.01642990e-01, -2.36861014e+00, ...,
           4.06775951e-01,  1.98266029e-01, -2.85190612e-01],
         [ 1.08131256e+01, -4.02826786e-01, -2.75746679e+00, ...,
          -1.08381718e-01,  2.26056725e-01,  2.94125646e-01],
         [ 1.03176470e+01, -1.01311028e+00, -2.88519478e+00, ...,
          -6.89408720e-01, -8.34803283e-03,  4.25132155e-01]],
 
        [[-3.81814718e-01, -3.81814718e-01, -3.81814718e-01, ...,
          -3.81814718e-01, -3.81814718e-01, -3.81814718e-01],
         [-1.11590952e-01, -1.11966029e-01, -1.12523913e-01, ...,
          -1.